In [31]:
import pandas as pd
import psycopg2

In [46]:
def create_database():
    conn =psycopg2.connect("host=localhost dbname=postgres user=postgres password=root")
    conn.set_session(autocommit=True)
    cur=conn.cursor()
    
    cur.execute("DROP DATABASE IF EXISTS accounts")
    cur.execute("CREATE DATABASE accounts")
    
    conn.close()
    
    conn =psycopg2.connect("host=localhost dbname=accounts user=postgres password=root")
    cur=conn.cursor()
    
    return cur,conn

In [33]:
def drop_tables(cur,conn):
    for q in drop_table_queries:
        cur.execute(q)
        conn.commit()

In [34]:
def create_tables(cur,conn):
    for q in create_table_queries:
        cur.execute(q)
        conn.commit()

In [8]:
AccountsCountry = pd.read_csv("./Wealth-AccountsCountry.csv")

In [9]:
AccountsCountry.head()

Code                  Long Name         Income Group  \
0  ALB        Republic of Albania  Upper middle income   
1  ARG         Argentine Republic  Upper middle income   
2  ARM        Republic of Armenia  Upper middle income   
3  AUS  Commonwealth of Australia          High income   
4  AUT        Republic of Austria          High income   

                      Region Lending category Other groups      Currency Unit  \
0      Europe & Central Asia             IBRD          NaN       Albanian lek   
1  Latin America & Caribbean             IBRD          NaN     Argentine peso   
2      Europe & Central Asia             IBRD          NaN      Armenian dram   
3        East Asia & Pacific              NaN          NaN  Australian dollar   
4      Europe & Central Asia              NaN    Euro area               Euro   

                            Latest population census  \
0                                    2020 (expected)   
1                                    2020 (expected)   
2                                    2020 (expected)   
3                                               2016   
4  2011. Population figures compiled from adminis...   

                      Latest household survey  \
0      Demographic and Health Survey, 2017/18   
1  Multiple Indicator Cluster Survey, 2019/20   
2      Demographic and Health Survey, 2015/16   
3                                         NaN   
4                                         NaN   

                                       Special Notes  ...  \
0                                                NaN  ...   
1                                                NaN  ...   
2                                                NaN  ...   
3  Fiscal year end: June 30; reporting period for...  ...   
4  A simple multiplier is used to convert the nat...  ...   

   Source of most recent Income and expenditure data  \
0  Living Standards Measurement Study Survey (LSM...   
1            Integrated household survey (IHS), 2016   
2            Integrated household survey (IHS), 2016   
3     Expenditure survey/budget survey (ES/BS), 2010   
4                           Income survey (IS), 2015   

   Vital registration complete Latest agricultural census  \
0                          Yes                       2012   
1                          Yes                       2008   
2                          Yes                       2014   
3                          Yes                  2015-2016   
4                          Yes                       2010   

  Latest industrial data Latest trade data Latest water withdrawal data  \
0                 2013.0            2018.0                       2006.0   
1                 2002.0            2018.0                       2011.0   
2                    NaN            2018.0                       2012.0   
3                 2013.0            2018.0                       2013.0   
4                 2014.0            2018.0                       2010.0   

  2-alpha code WB-2 code Table Name Short Name  
0           AL        AL    Albania    Albania  
1           AR        AR  Argentina  Argentina  
2           AM        AM    Armenia    Armenia  
3           AU        AU  Australia  Australia  
4           AT        AT    Austria    Austria  

[5 rows x 31 columns]

In [60]:
AccountsCountry.columns

Index(['Code', 'Long Name', 'Income Group', 'Region', 'Lending category',
       'Other groups', 'Currency Unit', 'Latest population census',
       'Latest household survey', 'Special Notes',
       'National accounts base year', 'National accounts reference year',
       'System of National Accounts', 'SNA price valuation',
       'Alternative conversion factor', 'PPP survey years',
       'Balance of Payments Manual in use', 'External debt Reporting status',
       'System of trade', 'Government Accounting concept',
       'IMF data dissemination standard',
       'Source of most recent Income and expenditure data',
       'Vital registration complete', 'Latest agricultural census',
       'Latest industrial data', 'Latest trade data',
       'Latest water withdrawal data', '2-alpha code', 'WB-2 code',
       'Table Name', 'Short Name'],
      dtype='object')

In [78]:
# Remove rows where 'Code' is null
AccountsCountry = AccountsCountry[AccountsCountry['Code'].notnull()]

# Print the unique rows
AccountsCountry = AccountsCountry.sort_values('Currency Unit').drop_duplicates('Code', keep='first')

AccountsCountry_clean = AccountsCountry[['Code','Short Name','Table Name','Long Name',
                                         'Currency Unit']]

In [79]:
AccountsCountry_clean.head()

Code Short Name Table Name                  Long Name      Currency Unit
0  ALB    Albania    Albania        Republic of Albania       Albanian lek
1  ARG  Argentina  Argentina         Argentine Republic     Argentine peso
2  ARM    Armenia    Armenia        Republic of Armenia      Armenian dram
3  AUS  Australia  Australia  Commonwealth of Australia  Australian dollar
6  BHR    Bahrain    Bahrain         Kingdom of Bahrain     Bahraini dinar

In [104]:
AccountsData = pd.read_csv("./Wealth-AccountData.csv")
AccountsData.columns

Index(['Country Name', 'Country Code', 'Series Name', 'Series Code',
       '1995 [YR1995]', '1996 [YR1996]', '1997 [YR1997]', '1998 [YR1998]',
       '1999 [YR1999]', '2000 [YR2000]', '2001 [YR2001]', '2002 [YR2002]',
       '2003 [YR2003]', '2004 [YR2004]', '2005 [YR2005]', '2006 [YR2006]',
       '2007 [YR2007]', '2008 [YR2008]', '2009 [YR2009]', '2010 [YR2010]',
       '2011 [YR2011]', '2012 [YR2012]', '2013 [YR2013]', '2014 [YR2014]',
       '2015 [YR2015]', '2016 [YR2016]', '2017 [YR2017]', '2018 [YR2018]'],
      dtype='object')

In [106]:
AccountsData= AccountsData[['Country Name','Country Code','Series Name','1998 [YR1998]',
                                         '2003 [YR2003]','2008 [YR2008]','2013 [YR2013]','2018 [YR2018]']]
AccountsData_clean = AccountsData[AccountsData['Country Code'].notnull() & AccountsData['Series Name'].notnull()]
AccountsData_clean = AccountsData_clean.drop_duplicates()

In [108]:
AccountsData_clean.head()

Country Name Country Code  \
0      Albania          ALB   
1      Albania          ALB   
2      Albania          ALB   
3      Albania          ALB   
4      Albania          ALB   

                                         Series Name 1998 [YR1998]  \
0                  Human capital (constant 2018 US$)      3.88E+10   
1       Human capital per capita (constant 2018 US$)      12399.48   
2  Human capital per capita, employed female (con...      3013.391   
3  Human capital per capita, employed male (const...      5901.072   
4  Human capital per capita, female (constant 201...      4191.445   

  2003 [YR2003]  2008 [YR2008]  2013 [YR2013] 2018 [YR2018]  
0      5.21E+10   6.340000e+10   7.160000e+10      8.12E+10  
1      17132.03   2.152357e+04   2.473162e+04      28333.68  
2       2016.02   2.664126e+03   2.954273e+03      3312.927  
3      10641.06   1.423203e+04   1.681013e+04      19245.19  
4       2728.79   3.393761e+03   3.696744e+03      4161.137

In [109]:
AccountsData_clean.columns

Index(['Country Name', 'Country Code', 'Series Name', '1998 [YR1998]',
       '2003 [YR2003]', '2008 [YR2008]', '2013 [YR2013]', '2018 [YR2018]'],
      dtype='object')

In [23]:
AccountsSeries = pd.read_csv("./Wealth-AccountSeries.csv")

In [24]:
AccountsSeries.columns

Index(['Code', 'Indicator Name', 'Long definition', 'Source', 'Topic',
       'Unit of measure', 'Periodicity', 'Reference period',
       'Statistical concept and methodology', 'Previous Indicator Code',
       'Previous Indicator Name'],
      dtype='object')

In [98]:
AccountsSeries = AccountsSeries[AccountsSeries['Indicator Name'].notnull()]
AccountsSeries_clean = AccountsSeries[['Code','Topic','Indicator Name','Long definition','Source']]
AccountsSeries_clean = AccountsSeries_clean.drop_duplicates()

In [99]:
AccountsSeries_clean.head()

Code          Topic  \
0       NW.HCA.TO  Human capital   
1       NW.HCA.PC  Human capital   
2  NW.HCA.FEMP.PC  Human capital   
3  NW.HCA.MEMP.PC  Human capital   
4  NW.HCA.FEMA.PC  Human capital   

                                      Indicator Name  \
0                  Human capital (constant 2018 US$)   
1       Human capital per capita (constant 2018 US$)   
2  Human capital per capita, employed female (con...   
3  Human capital per capita, employed male (const...   
4  Human capital per capita, female (constant 201...   

                                     Long definition  \
0  Human capital is computed as the present value...   
1  Human capital is computed as the present value...   
2  Human capital is computed as the present value...   
3  Human capital is computed as the present value...   
4  Human capital is computed as the present value...   

                                              Source  
0  World Bank. 2021. The Changing Wealth of Natio...  
1  World Bank. 2021. The Changing Wealth of Natio...  
2  World Bank. 2021. The Changing Wealth of Natio...  
3  World Bank. 2021. The Changing Wealth of Natio...  
4  World Bank. 2021. The Changing Wealth of Natio...

In [47]:
cur, conn= create_database()

In [48]:
create_table_cmd =("""CREATE TABLE IF NOT EXISTS accountscountry(
country_code VARCHAR PRIMARY KEY,
short_name VARCHAR,
table_name VARCHAR,
long_name VARCHAR,
currency_unit VARCHAR
)""")

In [49]:
cur.execute(create_table_cmd)
conn.commit()

In [52]:
create_table_cmd =("""CREATE TABLE IF NOT EXISTS accountseries(
series_code VARCHAR,
topic VARCHAR,
indicator_name VARCHAR,
short_definition VARCHAR
)""")

cur.execute(create_table_cmd)
conn.commit()


In [111]:
cur.close()
conn.close()

In [113]:
create_table_cmd =("""CREATE TABLE IF NOT EXISTS accountsdata(
country_name VARCHAR,
country_code VARCHAR,
indicator_name VARCHAR,
year_1998 numeric,
year_2003 numeric,
year_2008 numeric,
year_2013 numeric,
year_2018 numeric
)""")

conn = psycopg2.connect(database="accounts", user="postgres", password="root", host="localhost", port="5432")
curr= conn.cursor()
curr.execute(create_table_cmd)
conn.commit()
curr.close()
conn.close()


In [92]:
accounts_country_table_insert=("""INSERT INTO accountscountry(
country_code,
short_name,
table_name,
long_name,
currency_unit)
VALUES (%s,%s,%s,%s,%s)""")

In [94]:
import psycopg2

# Establish a connection to the database
connection = psycopg2.connect(database="accounts", user="postgres", password="root", host="localhost", port="5432")

try:
    # Create a cursor object
    cursor = connection.cursor()

    # Begin a new transaction
    cursor.execute("BEGIN")

    # Iterate over the rows and insert data
    for i, row in AccountsCountry_clean.iterrows():
        cursor.execute("INSERT INTO accountscountry (country_code, short_name, table_name, long_name, currency_unit) VALUES (%s, %s, %s, %s, %s)", list(row))

    # Commit the transaction to make the changes persistent
    connection.commit()

except (Exception, psycopg2.DatabaseError) as error:
    # Rollback the transaction in case of any error
    connection.rollback()
    print("Error occurred:", error)

finally:
    # Close the cursor and connection
    cursor.close()
    connection.close()


In [114]:
accounts_data_table_insert=("""INSERT INTO accountsdata(
country_name,
country_code,
indicator_name,
year_1998,
year_2003,
year_2008,
year_2013,
year_2018)
VALUES (%s,%s,%s,%s,%s,%s,%s,%s)""")

In [131]:
 for row in AccountsData_clean.iterrows():
	print(list(row))

[0, Country Name                               Albania
Country Code                                   ALB
Series Name      Human capital (constant 2018 US$)
1998 [YR1998]                             3.88E+10
2003 [YR2003]                             5.21E+10
2008 [YR2008]                        63400000000.0
2013 [YR2013]                        71600000000.0
2018 [YR2018]                             8.12E+10
Name: 0, dtype: object]
[1, Country Name                                          Albania
Country Code                                              ALB
Series Name      Human capital per capita (constant 2018 US$)
1998 [YR1998]                                        12399.48
2003 [YR2003]                                        17132.03
2008 [YR2008]                                        21523.57
2013 [YR2013]                                        24731.62
2018 [YR2018]                                        28333.68
Name: 1, dtype: object]
[2, Country Name                        

Name: 415, dtype: object]
[416, Country Name                               Belarus
Country Code                                   BLR
Series Name      Human capital (constant 2018 US$)
1998 [YR1998]                             1.71E+11
2003 [YR2003]                             2.01E+11
2008 [YR2008]                       313000000000.0
2013 [YR2013]                       430000000000.0
2018 [YR2018]                             3.87E+11
Name: 416, dtype: object]
[417, Country Name                                          Belarus
Country Code                                              BLR
Series Name      Human capital per capita (constant 2018 US$)
1998 [YR1998]                                        16988.22
2003 [YR2003]                                        20539.46
2008 [YR2008]                                        32882.01
2013 [YR2013]                                        45461.46
2018 [YR2018]                                        40798.49
Name: 417, dtype: object]
[418, 

Name: 770, dtype: object]
[771, Country Name                                              Botswana
Country Code                                                   BWA
Series Name      Natural capital, nonrenewable assets: oil (con...
1998 [YR1998]                                                    0
2003 [YR2003]                                                    0
2008 [YR2008]                                                  0.0
2013 [YR2013]                                                  0.0
2018 [YR2018]                                                    0
Name: 771, dtype: object]
[772, Country Name                                              Botswana
Country Code                                                   BWA
Series Name      Natural capital, protected areas (constant 201...
1998 [YR1998]                                             2.94E+09
2003 [YR2003]                                             2.19E+09
2008 [YR2008]                                         2350000000.

Name: 1150, dtype: object]
[1151, Country Name                              Central African Republic
Country Code                                                   CAF
Series Name      Human capital per capita, self-employed male (...
1998 [YR1998]                                             82.99621
2003 [YR2003]                                             80.12189
2008 [YR2008]                                             74.86798
2013 [YR2013]                                              59.4906
2018 [YR2018]                                             70.37862
Name: 1151, dtype: object]
[1152, Country Name                              Central African Republic
Country Code                                                   CAF
Series Name      Human capital, employed female (constant 2018 ...
1998 [YR1998]                                             1.64E+09
2003 [YR2003]                                             1.73E+09
2008 [YR2008]                                         1490000

Name: 1536, dtype: object]
[1537, Country Name                                            Costa Rica
Country Code                                                   CRI
Series Name      Natural capital per capita, protected areas (c...
1998 [YR1998]                                             1955.754
2003 [YR2003]                                              1803.52
2008 [YR2008]                                             2014.739
2013 [YR2013]                                             2126.195
2018 [YR2018]                                             1874.957
Name: 1537, dtype: object]
[1538, Country Name                                            Costa Rica
Country Code                                                   CRI
Series Name      Natural capital per capita, renewable (constan...
1998 [YR1998]                                             15062.77
2003 [YR2003]                                             12771.31
2008 [YR2008]                                             132

...

Name: 5768, dtype: object]
[5769, Country Name                                              Russia
Country Code                                                 RUS
Series Name      Produced capital per capita (constant 2018 US$)
1998 [YR1998]                                           73856.01
2003 [YR2003]                                           72058.15
2008 [YR2008]                                           74415.67
2013 [YR2013]                                           76399.71
2018 [YR2018]                                           77549.21
Name: 5769, dtype: object]
[5770, Country Name                               Russia
Country Code                                  RUS
Series Name      Total wealth (constant 2018 US$)
1998 [YR1998]                            1.68E+13
2003 [YR2003]                            1.96E+13
2008 [YR2008]                    24200000000000.0
2013 [YR2013]                    25500000000000.0
2018 [YR2018]                            2.51E+13
Name: 5770, 

Name: 6183, dtype: object]
[6184, Country Name                          Solomon Islands
Country Code                                      SLB
Series Name      Produced capital (constant 2018 US$)
1998 [YR1998]                                1.65E+09
2003 [YR2003]                                1.32E+09
2008 [YR2008]                            1280000000.0
2013 [YR2013]                            1130000000.0
2018 [YR2018]                                1.04E+09
Name: 6184, dtype: object]
[6185, Country Name                                     Solomon Islands
Country Code                                                 SLB
Series Name      Produced capital per capita (constant 2018 US$)
1998 [YR1998]                                           4220.298
2003 [YR2003]                                            2950.74
2008 [YR2008]                                           2541.972
2013 [YR2013]                                           1973.279
2018 [YR2018]                                

Name: 6585, dtype: object]
[6586, Country Name                                           Tanzania
Country Code                                                TZA
Series Name      Natural capital, fisheries (constant 2018 US$)
1998 [YR1998]                                          6.03E+08
2003 [YR2003]                                          1.02E+09
2008 [YR2008]                                       147000000.0
2013 [YR2013]                                       608000000.0
2018 [YR2018]                                          3.16E+08
Name: 6586, dtype: object]
[6587, Country Name                                              Tanzania
Country Code                                                   TZA
Series Name      Natural capital, forests: ecosystem services (...
1998 [YR1998]                                             2.36E+10
2003 [YR2003]                                             2.50E+10
2008 [YR2008]                                        27500000000.0
2013 [YR2013]     

Name: 6970, dtype: object]
[6971, Country Name                                                Uganda
Country Code                                                   UGA
Series Name      Human capital per capita, employed male (const...
1998 [YR1998]                                             1373.308
2003 [YR2003]                                             1629.078
2008 [YR2008]                                             1851.513
2013 [YR2013]                                             2274.144
2018 [YR2018]                                             2475.903
Name: 6971, dtype: object]
[6972, Country Name                                                Uganda
Country Code                                                   UGA
Series Name      Human capital per capita, female (constant 201...
1998 [YR1998]                                             924.2839
2003 [YR2003]                                             1221.852
2008 [YR2008]                                             131

Name: 7308, dtype: object]
[7309, Country Name                                             Venezuela
Country Code                                                   VEN
Series Name      Natural capital per capita, protected areas (c...
1998 [YR1998]                                             3159.778
2003 [YR2003]                                             2421.275
2008 [YR2008]                                             2450.235
2013 [YR2013]                                             2272.591
2018 [YR2018]                                              2044.94
Name: 7309, dtype: object]
[7310, Country Name                                             Venezuela
Country Code                                                   VEN
Series Name      Natural capital per capita, renewable (constan...
1998 [YR1998]                                             7909.415
2003 [YR2003]                                             5874.018
2008 [YR2008]                                             568

In [90]:
accounts_series_table_insert=("""INSERT INTO accountseries(
series_code,
topic,
indicator_name,
short_definition)
VALUES (%s,%s,%s,%s)""")

In [100]:
for i,row in AccountsSeries_clean.iterrows():
    print(list(row))

['NW.HCA.TO', 'Human capital', 'Human capital (constant 2018 US$)', 'Human capital is computed as the present value of future earnings for the working population over their lifetimes. Values are measured at market exchange rates in constant 2018 US dollars, using a country-specific GDP deflator.', 'World Bank. 2021. The Changing Wealth of Nations 2021: Managing Assets for the Future. Washington, DC: World Bank. doi:10.1596/978-1-4648-1590-4.']
['NW.HCA.PC', 'Human capital', 'Human capital per capita (constant 2018 US$)', 'Human capital is computed as the present value of future earnings for the working population over their lifetimes. Values are measured at market exchange rates in constant 2018 US dollars, using a country-specific GDP deflator.', 'World Bank. 2021. The Changing Wealth of Nations 2021: Managing Assets for the Future. Washington, DC: World Bank. doi:10.1596/978-1-4648-1590-4.']
['NW.HCA.FEMP.PC', 'Human capital', 'Human capital per capita, employed female (constant 2018

In [102]:
# Establish a connection to the database
connection = psycopg2.connect(database="accounts", user="postgres", password="root", host="localhost", port="5432")

try:
    # Create a cursor object
    cursor = connection.cursor()

    # Begin a new transaction
    cursor.execute("BEGIN")

    # Iterate over the rows and insert data
    for i, row in AccountsSeries_clean.iterrows():
        values = [row['Code'], row['Topic'], row['Indicator Name'], row['Long definition']]
        cursor.execute(accounts_series_table_insert, values)

    # Commit the transaction to make the changes persistent
    connection.commit()

except (Exception, psycopg2.DatabaseError) as error:
    # Rollback the transaction in case of any error
    connection.rollback()
    print("Error occurred:", error)

finally:
    # Close the cursor and connection
    cursor.close()
    connection.close()
